In [15]:
import os
import sys

parent_dir = os.path.abspath(os.path.join(os.getcwd(), '..'))
sys.path.insert(0, f'{parent_dir}/model')
sys.path.insert(0, f'{parent_dir}')
sys.path.insert(0, f'{parent_dir}/evaluation')
import pickle
# from FlyOutput import FlyOutput
# import Plotters
import plotly.graph_objects as go
import numpy as np  
import Utils
from Frame import Frame
import torch
# import Plotter
# import Plotters

from Evaluation import Evaluation
import model_utils
# import matplotlib.pyplot as plt
import os
# %matplotlib qt

frame_num = 370
cam = 0
path_output = 'D:/Documents/gaussian_model_output/'
dict_path  = 'G:/My Drive/Research/gaussian_splatting/gaussian_splatting_input/evaluation/dict/frames_model_evaluation.pkl'
idx_iter = 0
model_name = 'fly_pitch_delta10_sweep_m40_40_try'
file_name = f'fly_model_scale_iter{idx_iter}'
input_dir = f'{path_output}/{model_name}'
path_to_mesh = 'D:/Documents/model_gaussian_splatting/model/mesh'  
with open(dict_path,'rb') as f:
    frames = pickle.load(f)



input_dir_ini = 'G:/My Drive/Research/gaussian_splatting/gaussian_splatting_input/evaluation'

with open(f'{input_dir_ini}/nominal_initial_angles.pkl', 'rb') as handle:
    nominal_initial_angles = pickle.load(handle)


In [16]:


letedict = {'num_of_bins' : 20,'perc_wing_for_le' : 1, 'wing_length_snip':0.27}
projection_tasks = [
    ("right_wing_tagged_le", "right_wing_boundary_le", "interest_on_bound_rw_le"),
    ("left_wing_tagged_le", "left_wing_boundary_le", "interest_on_bound_lw_le"),
    ("right_wing_boundary_le", "right_wing_tagged_le", "bound_on_interest_rw_le"),
    ("left_wing_boundary_le", "left_wing_tagged_le", "bound_on_interest_lw_le"),
    ("right_wing_tagged_te", "right_wing_boundary_te", "interest_on_bound_rw_te"),
    ("left_wing_tagged_te", "left_wing_boundary_te", "interest_on_bound_lw_te"),
    ("right_wing_boundary_te", "right_wing_tagged_te", "bound_on_interest_rw_te"),
    ("left_wing_boundary_te", "left_wing_tagged_te", "bound_on_interest_lw_te"),]

att_to_calc_interest = ["interest_on_bound_rw", "interest_on_bound_lw", "interest_right_wing_boundry","interest_left_wing_boundry"]
att_to_calc_bound = ["bound_on_interest_rw", "bound_on_interest_lw", "right_wing_boundary","left_wing_boundary"]

iteration = 1000
idx_iter = 0
all_frames = []


def calc_psi_from_gt(frame_eval, points):
    wing_span_right,wing_chord_right = frame_eval.wing_span_chord(points)
    normal_wing_right = np.cross(wing_span_right,wing_chord_right) 
    return np.float32(-np.arccos(normal_wing_right[2]) * 180 / np.pi)

     

for mov_name in list(nominal_initial_angles.keys())[0:10]:

    # try:

        mov = int(mov_name.split('_')[1]) 
        frame0 = int(mov_name.split('_')[3]) 
        image_path =  f'G:/My Drive/Research/gaussian_splatting/gaussian_splatting_input/mov{mov}_2023_08_09_60ms/'
        file_name = f'fly_model_scale_iter{idx_iter}'
        interest_points_path = f'G:/My Drive/Research/gaussian_splatting/gaussian_splatting_input/evaluation/points/mov{mov}'

        with open(f'{input_dir}/results/{frame0}/{file_name}_results.pkl', 'rb') as handle:
            output_angles_weights = pickle.load(handle)

        frame_eval = Evaluation(interest_points_path,image_path,frame0,input_dir,output_angles_weights,frame0,iteration,file_name,letedict = letedict,frames_dict = frames)
        for source_attr, target_attr, output_attr in projection_tasks:
            frame_eval.get_projected_and_store(frame_eval, source_attr, target_attr, output_attr)



        nominal_initial_angles[mov_name]['right_wing_angles'][1] = calc_psi_from_gt(frame_eval, frame_eval.right_wing_tagged)
        nominal_initial_angles[mov_name]['left_wing_angles'][1] = np.float32(180-calc_psi_from_gt(frame_eval, frame_eval.left_wing_tagged))
        nominal_initial_angles[mov_name]['body_angles'][2] = nominal_initial_angles[mov_name]['body_angles'][2]

        


        root,body,right_wing,left_wing,list_joints_pitch_update = model_utils.initilize_skeleton_and_skin(path_to_mesh,skeleton_scale=1/1000)
        joint_list,skin,weights,bones = model_utils.build_skeleton(root,body,right_wing,left_wing)


        frames_per_cam = [Frame(image_path,frame0,cam_num,frames_dict = frames) for cam_num in range(4)]
        camera_pixel = np.vstack([frame.camera_center_to_pixel_ray(([frame.cm[0],frame.cm[1]])) for frame in  frames_per_cam])
        camera_center = np.vstack([frame.X0.T for frame in  frames_per_cam])
        cm_point = Utils.triangulate_least_square(camera_center,camera_pixel)
        ew_to_lab = list(frames[frame0][1].values())[0]['ew_to_lab']
        cm_point_lab = torch.tensor(ew_to_lab @ cm_point,device='cuda').float()


        # bod[0] = 180
        body_angles = torch.tensor(nominal_initial_angles[mov_name]['body_angles'],device='cuda')
        # body_angles[2] = -body_angles[2]
        right_wing_angles = torch.tensor(nominal_initial_angles[mov_name]['right_wing_angles'],device='cuda')
        # right_wing_angles[1] = -164
        left_wing_angles = torch.tensor(nominal_initial_angles[mov_name]['left_wing_angles'],device='cuda')

        cm_point_lab_t = cm_point_lab 

        means3D = model_utils.transform_pose(skin,weights,body_angles,list_joints_pitch_update,joint_list,bones,cm_point_lab_t,right_wing_angles,
                        left_wing_angles,torch.tensor(-0.0).cuda(),torch.tensor(-0.0).cuda(),
                        torch.tensor(-0.0).cuda(),torch.tensor(-0.0).cuda(),torch.tensor(-0.0).cuda(),torch.tensor(-0.0).cuda(),
                        torch.tensor(-0.0).cuda(),torch.tensor(-0.0).cuda())
        means3D_ew = torch.tensor(torch.tensor(ew_to_lab.T).cuda().float() @ means3D.T,device='cuda').float().T


        # frame_eval.body = means3D[:body.ptcloud_skin.shape[0],:].cpu()
        # frame_eval.right_wing = means3D[body.ptcloud_skin.shape[0]:body.ptcloud_skin.shape[0]+right_wing.ptcloud_skin.shape[0],:].cpu()
        # frame_eval.left_wing = means3D[body.ptcloud_skin.shape[0]+right_wing.ptcloud_skin.shape[0]:body.ptcloud_skin.shape[0]+right_wing.ptcloud_skin.shape[0] + left_wing.ptcloud_skin.shape[0],:].cpu()


        all_frames.append(frame_eval)
    # except:
    #     continue

path_to_save = 'G:/My Drive/Research/gaussian_splatting/gaussian_splatting_input/evaluation'
Utils.pickle_file(nominal_initial_angles,f'{path_to_save}/nominal_initial_angles.pkl' )


C:\Users\Roni\AppData\Local\Temp\ipykernel_5860\2743368442.py:78: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [89]:
len(all_frames)

154

In [84]:

path_to_save = 'G:/My Drive/Research/gaussian_splatting/gaussian_splatting_input/evaluation'
Utils.pickle_file(nominal_initial_angles,f'{path_to_save}/nominal_initial_angles.pkl' )


In [14]:
np.unique([int(mov_name.split('_')[3]) for mov_name in  list(nominal_initial_angles.keys())]).shape

len([int(mov_name.split('_')[3]) for mov_name in  list(nominal_initial_angles.keys())])

167

In [12]:
import plotly.graph_objects as go
import numpy as np


color_list = ['lime','crimson','magenta','magenta','dodgerblue','blue','blue','black','orange']
name_list = ['body','right wing','right wing le','right wing te','left wing','left wing le','left wing te','Ground truth','gaussian points']
size_list = [2,2,4,4,2,4,4,5,5]
framestart = 1031
frame_end = 1032
frames = range(framestart, frame_end)

output_path = f'{path_output}/{model_name}/animated_plot.html'

xyz_all_frames = np.vstack([frame.xyz_rotated for frame in all_frames])

# === HELPERS ===

def create_scatter3d(xyz, color,name,size = 2):
    """Create a single 3D scatter trace for a specific part."""
    return go.Scatter3d(
        x=xyz[:, 0],
        y=xyz[:, 1],
        z=xyz[:, 2],
        mode="markers",
        name = name,
        marker=dict(size=size, opacity=1, color=color, colorscale='gray'),
    )


def get_global_bounds(xyz_list):
    """Compute global min and max coordinates over all frames for consistent axis scaling."""
    return np.min(xyz_list, axis=0), np.max(xyz_list, axis=0)


def create_frame(parts_list, color_list,size_list, frame_name,name_list):
    """Create one animation frame with all parts for a given timestep."""
    data = [
        create_scatter3d(part, color,name,size)
        for part, color,size,name in zip(parts_list, color_list, size_list,name_list)
    ]
    return go.Frame(data=data, name=frame_name)


def create_play_pause_buttons():
    """Return Play/Pause button definitions for animation."""
    return [
        {
            "buttons": [
                {
                    "args": [None, {"frame": {"duration": 100, "redraw": True}, "fromcurrent": True}],
                    "label": "Play",
                    "method": "animate",
                },
                {
                    "args": [[None], {"frame": {"duration": 0, "redraw": True}, "mode": "immediate"}],
                    "label": "Pause",
                    "method": "animate",
                },
            ],
            "direction": "left",
            "pad": {"r": 10, "t": 87},
            "showactive": False,
            "type": "buttons",
            "x": 0.1,
            "xanchor": "right",
            "y": 0,
            "yanchor": "top",
        }
    ]

def create_slider(frame_nums):
    """Create a slider using actual frame numbers."""
    return [
        {
            "active": 0,
            "steps": [
                {
                    "args": [[str(i)], {"frame": {"duration": 100, "redraw": True}, "mode": "immediate"}],
                    "label": str(frame_num),
                    "method": "animate",
                }
                for i, frame_num in enumerate(frame_nums)
            ],
        }
    ]


# === MAIN FUNCTION ===

def create_3d_animation(frames_list, color_list,xyz_all_frames,size_list,name_list):
    """Build and show the 3D animation."""
    # frame_nums = [f.frame_num for f in frames_list[framestart - frame0:frame_end - frame0]]
    frame_nums = [frame.frame_num for frame in all_frames]
    min_xyz, max_xyz = get_global_bounds(xyz_all_frames)

    # Initial frame data
    intial_parts = [frames_list[0].body,frames_list[0].right_wing,frames_list[0].right_wing_le,frames_list[0].right_wing_te,frames_list[0].left_wing,frames_list[0].left_wing_le,frames_list[0].left_wing_te, frames_list[0].rotated_points_3d]
    initial_data = [
        create_scatter3d(part, color,name,size)
        for  part,color,size,name in zip(intial_parts, color_list,size_list,name_list)
    ]
    bounding_box_trace = go.Scatter3d(

    mode='markers',
    marker=dict(size=0.1, color='rgba(0,0,0,0)'),
    showlegend=False
    )
    initial_data.append(bounding_box_trace)
    # Create frames for animation
    frames_data = [
        create_frame([xyz_frame.body,xyz_frame.right_wing,xyz_frame.right_wing_le,xyz_frame.right_wing_te,xyz_frame.left_wing,xyz_frame.left_wing_le,xyz_frame.left_wing_te, xyz_frame.rotated_points_3d], color_list,size_list, str(i),name_list)
        for i, xyz_frame in enumerate(frames_list)
    ]

    # Build full figure
    fig = go.Figure(
        data=initial_data,
        layout=go.Layout(
            scene=dict(
                xaxis_title="X",
                yaxis_title="Y",
                zaxis_title="Z",
            ),
            updatemenus=create_play_pause_buttons(),
            sliders=create_slider(frame_nums),
        ),
        frames=frames_data,
    )

    fig.show()
    fig.write_html(output_path)
    print(f"Saved animation to: {output_path}")


create_3d_animation(all_frames, color_list,xyz_all_frames,size_list,name_list)




    # point_3d_per_frame.append(np.vstack(points_3d))
    # gaussians_interest_points.append(gaussian_points)

Saved animation to: D:/Documents/gaussian_model_output//fly_pitch_delta10_sweep_m40_40_try/animated_plot.html


In [56]:
all_frames[0].frame_num

1620

In [527]:
    import itertools
    yaw_grid = np.hstack(np.arange(0,360,30))
    roll_grid = np.hstack(np.arange(-30,30,10))
    psi_grid = np.hstack((np.arange(-160,0,30)))
    phi_grid = np.hstack((np.arange(-90,90,30)))

    roll_yaw = list(itertools.product(yaw_grid,roll_grid))
    psi_phi = list(itertools.product(psi_grid,phi_grid))
    # roll_yaw = roll_grid
    # pitch_grid = np.hstack((0.0,np.arange(-20,0,5),np.arange(5,20,5)))
    roll_yaw = roll_yaw + psi_phi

In [530]:
108-36

72

In [54]:
frame = 370
color = frames_list[frame - frame0].color
idx_part = frames_list[frame - frame0].idx_parts


grayscale = (color[:,0] - color[:,0].min()) / (color[:,0].max() - color[:,0].min())

opacity = frames_list[frame - frame0].opacity * grayscale
# grayscale = grayscale[grayscale <1]

frame = frames_list[frame-frame0]
fig = go.Figure()
Plotters.scatter3d(fig,frame.body,'green',3,'body',show_colorbar = False)
Plotters.scatter3d(fig,frame.right_wing,opacity[idx_part[1]],2,'right wing',show_colorbar = False)
Plotters.scatter3d(fig,frame.left_wing,opacity[idx_part[2]],2,'left wing',show_colorbar = False)
Plotters.scatter3d(fig,frame.rotated_points_3d[7:8,:],'blue',5,'interest',show_colorbar = False)
# Plotters.scatter3d(fig,frames_list[frame-frame0].gaussian_closest_to_interest,'orange',5,'interest gauss',show_colorbar = False)
Plotters.scatter3d(fig,frame.right_wing_le,'magenta',4,'le',show_colorbar = False)
Plotters.scatter3d(fig,frame.right_wing_te,'cyan',4,'te',show_colorbar = False)

Plotters.scatter3d(fig,frame.left_wing_le,'magenta',4,'le',show_colorbar = False)
Plotters.scatter3d(fig,frame.left_wing_te,'cyan',4,'te',show_colorbar = False)


t = np.linspace(-0.001, 0.0015, 100)  # Small range since your data seems very small-scale

r_line_points = frame.right_wing_origin + t[:, np.newaxis] * frame.right_wing_span
l_line_points = frame.left_wing_origin + t[:, np.newaxis] * frame.left_wing_span
idx_closest = np.unique([np.argsort(frame.dist_points(point,frame.body))[0:10] for point in r_line_points])
# idx_origin = np.argmin(np.dot(frame.body[idx_closest,:],frame.right_wing_direction))
idx_origin = np.argmax([np.min(np.dot(frame.body[idx_closest,:],r_line_points.T)) for idx_closest in idx_closest])
idx_origin


Plotters.scatter3d(fig,r_line_points,'orange',3,'wing',show_colorbar = False)
Plotters.scatter3d(fig,l_line_points,'orange',3,'wing',show_colorbar = False)
# Plotters.scatter3d(fig,np.atleast_2d(frame.body[idx_closest[idx_origin],:]),'black',10,'wing',show_colorbar = False)

# Plotters.scatter3d(fig,frame.gaussian_closest_to_interest,'orange',5,'interest gauss',show_colorbar = False)
# Plotters.scatter3d(fig,frame.body_interest_gaussian,'orange',5,'interest gauss',show_colorbar = False)
# dot_on_le = np.dot(-frame.right_wing_direction,frame.right_wing_le.T)
# length = (np.max(dot_on_le) - np.min(dot_on_le))
# lt20p = frame.right_wing_le[(dot_on_le  - np.min(dot_on_le))> length*0.1,:]
# Plotters.scatter3d(fig,frame.rotated_points_3d[8:16],'orange',3,'interest gauss',show_colorbar = False)
# Plotters.scatter3d(fig, np.vstack((np.mean(frame.bottom,axis = 0) - frame.xbody*2/1000,np.mean(frame.body,axis = 0) + frame.xbody*2/1000)),'black',5,'x',mode = 'markers+lines') 
# Plotters.scatter3d(fig, lt20p,'magenta',5,'x') 
# Plotters.scatter3d(fig,bod_ax_top,'black',3,'body',show_colorbar = False)

# Plotters.scatter3d(fig, np.atleast_2d(frame.interest_on_xbody),'black',10,'inter_on_body',mode = 'markers+lines') 
# Plotters.scatter3d(fig, frame.rotated_points_3d[16:,:],'black',10,'inter',mode = 'markers+lines') 


# fig.show()

# ax = None
# ax = Plotters.plot_projections(frame.interest_points_3d[:,:],frame.frames,color = 'magenta',ax = ax, size = 5)
# ax = Plotters.plot_projections(frame.gaussian_closest_to_interest_ew[:,:],frame.frames,color = 'orange',ax = ax, size = 5)
# # ax = Plotters.plot_projections(frame.body_interest_gaussian_ew[:,:],frame.frames,color = 'orange',ax = ax, size = 5)

# ax = None
# ax = Plotters.plot_projections(frame.right_wing_ew[:,:],frame.frames,color = 'red',ax = ax, size = 5)
# ax = Plotters.plot_projections(frame.left_wing_ew[:,:],frame.frames,color = 'blue',ax = ax, size = 5)


AttributeError: 'FlyOutput' object has no attribute 'dist_points'

In [ ]:
dot_on_le = np.dot(frame.right_wing_direction,frame.right_wing_le.T)
length = (np.max(dot_on_le) - np.min(dot_on_le))
lt20p = dot_on_le[dot_on_le > length*0.2,:]

0.002344680935456922

In [39]:
idx_origin = np.argmin([np.min(np.dot(frame.body[idx_closest,:],r_line_points.T)) for idx_closest in idx_closest])
idx_origin

89

In [ ]:
wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))
nrml = np.cross(frame.right_wing_span,frame.right_wing_chord)
pts_on_nrml = np.dot(wing_bound,nrml)

plt.figure(),plt.plot(pts_on_nrml)
std = np.std(pts_on_nrml)
mean = np.mean(pts_on_nrml)
plt.figure()
plt.plot((pts_on_nrml - mean)/std)


In [11]:
wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))
nrml = np.cross(frame.right_wing_span,frame.right_wing_chord)
pts_on_nrml = np.dot(wing_bound,nrml)
std = np.std(pts_on_nrml)
mean = np.mean(pts_on_nrml)
wing_bound = wing_bound[((pts_on_nrml - mean)/std) < 1.5]

indices_wing_bound = frame.cyclic_sort(wing_bound,frame.right_wing_span,frame.right_wing_chord)
points_2d = Utils.project_to_plane(wing_bound[indices_wing_bound], np.mean(wing_bound[indices_wing_bound],axis = 0), frame.right_wing_span,frame.right_wing_chord)
plt.figure()
plt.plot(points_2d[:,0],points_2d[:,1])

plt.figure()
plt.plot(points_2d)

In [ ]:

wing_gs,interest_rw,interest_lw = frame.zsocre_ol_calc_indices()


In [21]:
from scipy.signal import savgol_filter


frame = frames_list[-1]
wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))
nrml = np.cross(frame.right_wing_span,frame.right_wing_chord)
pts_on_nrml = np.dot(wing_bound,nrml)
std = np.std(pts_on_nrml)
mean = np.mean(pts_on_nrml)
wing_bound = wing_bound[((pts_on_nrml - mean)/std) < 1.5]

indices_wing_bound = frame.cyclic_sort(wing_bound,frame.right_wing_span,frame.right_wing_chord)
points_2d = Utils.project_to_plane(wing_bound[indices_wing_bound], np.mean(wing_bound[indices_wing_bound],axis = 0), frame.right_wing_span,frame.right_wing_chord)


x = savgol_filter(points_2d[:,0], 15, 2)
y = savgol_filter(points_2d[:,1], 15, 2)


plt.scatter(points_2d[:,0],points_2d[:,1])

plt.scatter(x,y)

In [ ]:
frame = frames_list[-1]
wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))
nrml = np.cross(frame.right_wing_span,frame.right_wing_chord)
pts_on_nrml = np.dot(wing_bound,nrml)
std = np.std(pts_on_nrml)
mean = np.mean(pts_on_nrml)
wing_bound = wing_bound[((pts_on_nrml - mean)/std) < 1.5]

indices_wing_bound = frame.cyclic_sort(wing_bound,frame.right_wing_span,frame.right_wing_chord)
points_2d = Utils.project_to_plane(wing_bound[indices_wing_bound], np.mean(wing_bound[indices_wing_bound],axis = 0), frame.right_wing_span,frame.right_wing_chord)



wing_bound = wing_bound[indices_wing_bound]
pts_to_fit = [wing_bound[k:k+3] for k in range(0,wing_bound.shape[0],3)]

fit = []
for pts in pts_to_fit[:-1]: 

    dists = np.linalg.norm(np.diff(pts, axis=0), axis=1)
    t = np.insert(np.cumsum(dists), 0, 0)  # insert 0 at the beginning
    p = np.polyfit(t, pts, 2)
    t_fit = np.linspace(t[0], t[-1], 1000)
    fit_xyz = np.vstack([np.polyval(p, t_fit) for p in p.T]).T
    fit.append(fit_xyz)
fit = np.vstack(fit)
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
ax.plot(wing_bound[:,0], wing_bound[:,1], wing_bound[:,2], 'ro', label='Original points')
ax.plot(fit[:,0], fit[:,1], fit[:,2], 'm-', label='Fitted 2nd order curve')
ax.legend()
plt.show()

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned



In [26]:
fit.shape

(21000, 3)

In [ ]:
from math import atan2
normal_to_wing = np.cross(frame.right_wing_span,frame.right_wing_chord)

wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))



frameidx = 4
frame = frames_list[frameidx]
wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))
interest = frames_list[frameidx].rotated_points_3d[frame.interest_right_wing_boundry,:]



points_2d = Utils(wing_bound, np.mean(wing_bound,axis = 0), frame.right_wing_span, frame.right_wing_chord)
indices = Utils.rotational_sort(points_2d, np.mean(points_2d,axis = 0), clockwise=True)
# indices2 = rotational_sort(points_2d, np.mean(points_2d,axis = 0), clockwise=True)


wing_bound
fig = go.Figure()
# Plotters.scatter3d(fig,frame.right_wing,'red',3,'body',show_colorbar = False)
# Plotters.scatter3d(fig,interest[indices,:],'black',3,'interest',show_colorbar = False,mode='markers+lines')
Plotters.scatter3d(fig,wing_bound[indices2,:],'blue',3,'gs',show_colorbar = False,mode='markers+lines')
Plotters.scatter3d(fig,np.atleast_2d(frame.right_wing_origin),'blue',10,'gs',show_colorbar = False,mode='markers+lines')

fig.show()


In [30]:
from math import atan2

def argsort(seq):
    #http://stackoverflow.com/questions/3382352/equivalent-of-numpy-argsort-in-basic-python/3382369#3382369
    #by unutbu
    #https://stackoverflow.com/questions/3382352/equivalent-of-numpy-argsort-in-basic-python 
    # from Boris Gorelik
    return sorted(range(len(seq)), key=seq.__getitem__)

def rotational_sort(list_of_xy_coords, centre_of_rotation_xy_coord, clockwise=True):
    cx,cy=centre_of_rotation_xy_coord
    angles = [atan2(x-cx, y-cy) for x,y in list_of_xy_coords]
    indices = argsort(angles)
    # if clockwise:
    #     return [list_of_xy_coords[i] for i in indices]
    # else:
    #     return [list_of_xy_coords[i] for i in indices[::-1]]
    return indices

frameidx = 4
frame = frames_list[frameidx]
wing_bound = np.vstack((frame.right_wing_le,frame.right_wing_te))
interest = frames_list[frameidx].rotated_points_3d[frame.interest_right_wing_boundry,:]
indices = rotational_sort(interest[:,[1,2]], np.mean(interest[:,[1,2]],axis = 0), clockwise=True)
indices2 = rotational_sort(wing_bound[:,[1,2]], np.mean(wing_bound[:,[1,2]],axis = 0), clockwise=True)


wing_bound
fig = go.Figure()
# Plotters.scatter3d(fig,frame.right_wing,'red',3,'body',show_colorbar = False)
Plotters.scatter3d(fig,interest[indices,:],'black',3,'interest',show_colorbar = False,mode='markers+lines')
Plotters.scatter3d(fig,wing_bound[indices2,:],'blue',3,'gs',show_colorbar = False,mode='markers+lines')
Plotters.scatter3d(fig,np.atleast_2d(frame.right_wing_origin),'blue',10,'gs',show_colorbar = False,mode='markers+lines')

fig.show()


In [59]:
import numpy as np
import matplotlib.pyplot as plt

# Your 3D points (N x 3)
points = interest[indices,:]
# points = wing_bound[indices2,:]

pts_to_fit = [points[k:k+3] for k in range(0,points.shape[0],3)]
# pts_to_fit = [points[k:k+5] for k in range(0,points.shape[0],5)]


fit = []
for pts in pts_to_fit[:-1]: 
    # Step 1: Generate parameter t (cumulative distance)
    dists = np.linalg.norm(np.diff(pts, axis=0), axis=1)
    t = np.insert(np.cumsum(dists), 0, 0)  # insert 0 at the beginning

    # Step 2: Fit a 2nd degree polynomial separately for x(t), y(t), z(t)
    degree = 2
    px = np.polyfit(t, pts[:,0], degree)
    py = np.polyfit(t, pts[:,1], degree)
    pz = np.polyfit(t, pts[:,2], degree)

    # To evaluate the fitted curve:
    t_fit = np.linspace(t[0], t[-1], 1000)
    x_fit = np.polyval(px, t_fit)
    y_fit = np.polyval(py, t_fit)
    z_fit = np.polyval(pz, t_fit)
    fit.append(np.vstack((x_fit, y_fit, z_fit)))
fit = np.hstack(fit).T
# Plotting
# fig = plt.figure()
# ax = fig.add_subplot(111, projection='3d')
# ax.plot(points[:,0], points[:,1], points[:,2], 'ro', label='Original points')
# ax.plot(fit[:,0], fit[:,1], fit[:,2], 'm-', label='Fitted 2nd order curve')
# ax.legend()
# plt.show()


In [60]:
import numpy as np
import matplotlib.pyplot as plt

# Your 3D points (N x 3)
points = interest[indices,:]
points = wing_bound[indices2,:]

pts_to_fit = [points[k:k+3] for k in range(0,points.shape[0],3)]
# pts_to_fit = [points[k:k+5] for k in range(0,points.shape[0],5)]


fit2 = []
for pts in pts_to_fit[:-1]: 
    # Step 1: Generate parameter t (cumulative distance)
    dists = np.linalg.norm(np.diff(pts, axis=0), axis=1)
    t = np.insert(np.cumsum(dists), 0, 0)  # insert 0 at the beginning

    # Step 2: Fit a 2nd degree polynomial separately for x(t), y(t), z(t)
    degree = 2
    px = np.polyfit(t, pts[:,0], degree)
    py = np.polyfit(t, pts[:,1], degree)
    pz = np.polyfit(t, pts[:,2], degree)

    # To evaluate the fitted curve:
    t_fit = np.linspace(t[0], t[-1], 1000)
    x_fit = np.polyval(px, t_fit)
    y_fit = np.polyval(py, t_fit)
    z_fit = np.polyval(pz, t_fit)
    fit2.append(np.vstack((x_fit, y_fit, z_fit)))
fit2 = np.hstack(fit2).T
# Plotting
# fig = plt.figure()
# ax = fig.add_subplot(111, projection='3d')
# ax.plot(points[:,0], points[:,1], points[:,2], 'ro', label='Original points')
# ax.plot(fit[:,0], fit[:,1], fit[:,2], 'm-', label='Fitted 2nd order curve')
# ax.legend()
# plt.show()


c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarning:

Polyfit may be poorly conditioned

c:\Users\Roni\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3460: RankWarni

In [61]:

def dist_points(x1,x2):
    return np.sqrt(np.sum((x1 - x2)**2, axis = 1))

gaussian_closest_to_interest = np.vstack((fit2[np.argmin(dist_points(fit2,point)),:] for point in fit))
fitted_closest_to_gauss = np.vstack((fit[np.argmin(dist_points(fit,point)),:] for point in fit2))


plt.figure()
plt.hist(1000*dist_points(gaussian_closest_to_interest,fit))

plt.figure()
plt.hist(1000*dist_points(fitted_closest_to_gauss,fit2))

C:\Users\Roni\AppData\Local\Temp\ipykernel_14272\387352763.py:4: FutureWarning:

arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.

C:\Users\Roni\AppData\Local\Temp\ipykernel_14272\387352763.py:5: FutureWarning:

arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.



(array([3399., 5420., 5358., 4233., 2123.,  666.,  294.,  169.,  161.,
         177.]),
 array([0.00934659, 0.03537276, 0.06139894, 0.08742511, 0.11345128,
        0.13947745, 0.16550363, 0.1915298 , 0.21755597, 0.24358214,
        0.26960831]),
 <BarContainer object of 10 artists>)

In [ ]:


def dist_points(x1,x2):
    return np.sqrt(np.sum((x1 - x2)**2, axis = 1))

gaussian_closest_to_interest = np.vstack((fit[np.argmin(dist_points(fit,point)),:] for point in wing_bound))


    def closest_point_to_interest_boundary(self,wing_boundary,points):   

        gaussian_closest_to_interest = np.vstack((wing_boundary[np.argmin(self.dist_points(wing_boundary,point)),:] for point in points))
        gaussian_closest_to_interest_ew = (self.ew_to_lab.T @ np.vstack(gaussian_closest_to_interest).T).T
        dist_gaus_interest = self.dist_points(gaussian_closest_to_interest[1:,:],gaussian_closest_to_interest[0:-1,:])
        dist_interest = self.dist_points(points[1:,:],points[0:-1,:])   
        return  gaussian_closest_to_interest,gaussian_closest_to_interest_ew,dist_gaus_interest,dist_interest
